In [ ]:
from __future__ import absolute_import

In [44]:
from __future__ import division

In [45]:
from __future__ import print_function

In [46]:
import numpy as np

In [47]:
import tensorflow as tf

In [48]:
tf.logging.set_verbosity(tf.logging.INFO)

In [49]:
def cnn_model_fn(features, labels, mode):
  """Model function for CNN."""
  # Input Layer
  # Reshape X to 4-D tensor: [batch_size, width, height, channels]
  # MNIST images are 28x28 pixels, and have one color channel
  input_layer = tf.reshape(features["x"], [-1, 28, 28, 1])

  # Convolutional Layer #1
  # Computes 32 features using a 5x5 filter with ReLU activation.
  # Padding is added to preserve width and height.
  # Input Tensor Shape: [batch_size, 28, 28, 1]
  # Output Tensor Shape: [batch_size, 28, 28, 32]
  conv1 = tf.layers.conv2d(
      inputs=input_layer,
      filters=32,
      kernel_size=[5, 5],
      padding="same",
      activation=tf.nn.relu)

  # Pooling Layer #1
  # First max pooling layer with a 2x2 filter and stride of 2
  # Input Tensor Shape: [batch_size, 28, 28, 32]
  # Output Tensor Shape: [batch_size, 14, 14, 32]
  pool1 = tf.layers.max_pooling2d(inputs=conv1, pool_size=[2, 2], strides=2)

  # Convolutional Layer #2
  # Computes 64 features using a 5x5 filter.
  # Padding is added to preserve width and height.
  # Input Tensor Shape: [batch_size, 14, 14, 32]
  # Output Tensor Shape: [batch_size, 14, 14, 64]
  conv2 = tf.layers.conv2d(
      inputs=pool1,
      filters=64,
      kernel_size=[5, 5],
      padding="same",
      activation=tf.nn.relu)

  # Pooling Layer #2
  # Second max pooling layer with a 2x2 filter and stride of 2
  # Input Tensor Shape: [batch_size, 14, 14, 64]
  # Output Tensor Shape: [batch_size, 7, 7, 64]
  pool2 = tf.layers.max_pooling2d(inputs=conv2, pool_size=[2, 2], strides=2)
  
  # Convolutional Layer #3
  # Computes 128 features using a 5x5 filter.
  # Padding is added to preserve width and height.
  # Input Tensor Shape: [batch_size, 7, 7, 64]
  # Output Tensor Shape: [batch_size, 7, 7, 128]
  conv3 = tf.layers.conv2d(
      inputs=pool2,
      filters=128,
      kernel_size=[5, 5],
      padding="same",
      activation=tf.nn.relu)

  # Pooling Layer #3
  # Second max pooling layer with a 2x2 filter and stride of 2
  # Input Tensor Shape: [batch_size, 7, 7, 128]
  # Output Tensor Shape: [batch_size, 4, 4, 128]
  pool3 = tf.layers.max_pooling2d(inputs=conv3, pool_size=[2, 2], strides=2)
  
  # Convolutional Layer #4
  # Computes 256 features using a 5x5 filter.
  # Padding is added to preserve width and height.
  # Input Tensor Shape: [batch_size, 4, 4, 128]
  # Output Tensor Shape: [batch_size, 4, 4, 256]
  conv4 = tf.layers.conv2d(
      inputs=pool3,
      filters=256,
      kernel_size=[5, 5],
      padding="same",
      activation=tf.nn.relu)

  # Pooling Layer #2
  # Second max pooling layer with a 2x2 filter and stride of 2
  # Input Tensor Shape: [batch_size, 4, 4, 256]
  # Output Tensor Shape: [batch_size, 2, 2, 256]
  pool4 = tf.layers.max_pooling2d(inputs=conv4, pool_size=[2, 2], strides=2)

  # Flatten tensor into a batch of vectors
  # Input Tensor Shape: [batch_size, 7, 7, 64]
  # Output Tensor Shape: [batch_size, 7 * 7 * 64]
  pool4_flat = tf.reshape(pool4, [-1, 1 * 1 * 256])

  # Dense Layer
  # Densely connected layer with 1024 neurons
  # Input Tensor Shape: [batch_size, 7 * 7 * 64]
  # Output Tensor Shape: [batch_size, 1024]
  dense = tf.layers.dense(inputs=pool4_flat, units=1024, activation=tf.nn.relu)

  # Add dropout operation; 0.6 probability that element will be kept
  dropout = tf.layers.dropout(
      inputs=dense, rate=0.4, training=mode == tf.estimator.ModeKeys.TRAIN)

  # Logits layer
  # Input Tensor Shape: [batch_size, 1024]
  # Output Tensor Shape: [batch_size, 10]
  logits = tf.layers.dense(inputs=dropout, units=10)

  predictions = {
      # Generate predictions (for PREDICT and EVAL mode)
      "classes": tf.argmax(input=logits, axis=1),
      # Add `softmax_tensor` to the graph. It is used for PREDICT and by the
      # `logging_hook`.
      "probabilities": tf.nn.softmax(logits, name="softmax_tensor")
  }
  if mode == tf.estimator.ModeKeys.PREDICT:
    return tf.estimator.EstimatorSpec(mode=mode, predictions=predictions)

  # Calculate Loss (for both TRAIN and EVAL modes)
  loss = tf.losses.sparse_softmax_cross_entropy(labels=labels, logits=logits)

  # Configure the Training Op (for TRAIN mode)
  if mode == tf.estimator.ModeKeys.TRAIN:
    optimizer = tf.train.GradientDescentOptimizer(learning_rate=0.001)
    train_op = optimizer.minimize(
        loss=loss,
        global_step=tf.train.get_global_step())
    return tf.estimator.EstimatorSpec(mode=mode, loss=loss, train_op=train_op)

  # Add evaluation metrics (for EVAL mode)
  eval_metric_ops = {
      "accuracy": tf.metrics.accuracy(
          labels=labels, predictions=predictions["classes"])}
  return tf.estimator.EstimatorSpec(
      mode=mode, loss=loss, eval_metric_ops=eval_metric_ops)

In [55]:
def main(unused_argv):
  # Load training and eval data
  mnist = tf.contrib.learn.datasets.load_dataset("mnist")
  train_data = mnist.train.images  # Returns np.array
  train_labels = np.asarray(mnist.train.labels, dtype=np.int32)
  eval_data = mnist.test.images  # Returns np.array
  eval_labels = np.asarray(mnist.test.labels, dtype=np.int32)

  # Create the Estimator
  mnist_classifier = tf.estimator.Estimator(
      model_fn=cnn_model_fn, model_dir="/tmp/mnist_convnet_model3")

  # Set up logging for predictions
  # Log the values in the "Softmax" tensor with label "probabilities"
  tensors_to_log = {"probabilities": "softmax_tensor"}
  logging_hook = tf.train.LoggingTensorHook(
      tensors=tensors_to_log, every_n_iter=50)

  # Train the model
  train_input_fn = tf.estimator.inputs.numpy_input_fn(
      x={"x": train_data},
      y=train_labels,
      batch_size=100,
      num_epochs=None,
      shuffle=True)
  mnist_classifier.train(
      input_fn=train_input_fn,
      steps=20000,
      hooks=[logging_hook])

  # Evaluate the model and print results
  eval_input_fn = tf.estimator.inputs.numpy_input_fn(
      x={"x": eval_data},
      y=eval_labels,
      num_epochs=1,
      shuffle=False)
  eval_results = mnist_classifier.evaluate(input_fn=eval_input_fn)
  print(eval_results)

In [56]:
if __name__ == "__main__":
  tf.app.run()

Extracting MNIST-data\train-images-idx3-ubyte.gz
Extracting MNIST-data\train-labels-idx1-ubyte.gz
Extracting MNIST-data\t10k-images-idx3-ubyte.gz
Extracting MNIST-data\t10k-labels-idx1-ubyte.gz
INFO:tensorflow:Using default config.
INFO:tensorflow:Using config: {'_model_dir': '/tmp/mnist_convnet_model3', '_tf_random_seed': None, '_save_summary_steps': 100, '_save_checkpoints_steps': None, '_save_checkpoints_secs': 600, '_session_config': None, '_keep_checkpoint_max': 5, '_keep_checkpoint_every_n_hours': 10000, '_log_step_count_steps': 100, '_service': None, '_cluster_spec': <tensorflow.python.training.server_lib.ClusterSpec object at 0x0000021E8015D208>, '_task_type': 'worker', '_task_id': 0, '_global_id_in_cluster': 0, '_master': '', '_evaluation_master': '', '_is_chief': True, '_num_ps_replicas': 0, '_num_worker_replicas': 1}
INFO:tensorflow:Calling model_fn.
INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorflow:Graph was finalized.
INFO:t

INFO:tensorflow:loss = 2.3042946, step = 1
INFO:tensorflow:probabilities = [[0.09928091 0.09874074 0.10245944 0.10291298 0.0999033  0.09687223
  0.10259718 0.09761261 0.10040296 0.09921756]
 [0.09559608 0.09886202 0.10438935 0.10398077 0.0997234  0.09721848
  0.10331575 0.09967235 0.10040359 0.09683827]
 [0.09894848 0.09955524 0.10314882 0.10102329 0.09940071 0.09879009
  0.10100874 0.0990652  0.10114229 0.09791721]
 [0.09772786 0.09917914 0.10269788 0.10281547 0.09908473 0.09738305
  0.10194164 0.09922048 0.10062508 0.09932467]
 [0.09880766 0.09731205 0.10282493 0.10071493 0.10002712 0.0979885
  0.1045657  0.09821524 0.10116036 0.09838349]
 [0.09776425 0.09943698 0.10133924 0.10062104 0.09896557 0.10043015
  0.10163923 0.09990425 0.10019377 0.09970555]
 [0.0978372  0.09858246 0.10320786 0.10126491 0.10116512 0.0989674
  0.1008579  0.09899167 0.10114069 0.0979848 ]
 [0.09970201 0.09929482 0.10140281 0.103364   0.09947577 0.09932478
  0.10077085 0.09723695 0.10045708 0.09897085]
 [0.099

INFO:tensorflow:global_step/sec: 46.7706
INFO:tensorflow:probabilities = [[0.10031505 0.10010044 0.10298379 0.10205911 0.10104714 0.09687547
  0.10057528 0.0981204  0.09863935 0.09928401]
 [0.09813628 0.10028125 0.1012122  0.10218374 0.10106974 0.09916616
  0.10114137 0.0984085  0.09996754 0.09843326]
 [0.09796233 0.09930948 0.1024032  0.10335013 0.0986568  0.09813312
  0.10268014 0.09952355 0.09997918 0.09800213]
 [0.09984596 0.09939089 0.10311531 0.09964654 0.10034578 0.09753329
  0.10370021 0.09961605 0.09909755 0.09770853]
 [0.09889994 0.09629607 0.10158376 0.10189811 0.09960414 0.09875852
  0.10336938 0.09898221 0.10050981 0.10009807]
 [0.09780218 0.09815616 0.1029489  0.10122725 0.10286327 0.09723442
  0.10180413 0.09706146 0.10181773 0.09908449]
 [0.09992936 0.09827923 0.10276949 0.10077206 0.10048199 0.09883202
  0.1024161  0.09950146 0.10001831 0.09700004]
 [0.09991235 0.09865236 0.10270163 0.10050613 0.10253864 0.09775116
  0.10281198 0.09858767 0.09868082 0.09785724]
 [0.098

INFO:tensorflow:loss = 2.3023317, step = 101 (2.132 sec)
INFO:tensorflow:probabilities = [[0.09779496 0.09899947 0.10153346 0.10406974 0.09965308 0.09766179
  0.10260323 0.09924864 0.09977005 0.09866551]
 [0.0983555  0.10053669 0.10248617 0.10157728 0.09892871 0.09759041
  0.10337865 0.09877032 0.09989785 0.09847846]
 [0.09749454 0.10056247 0.10165897 0.10131706 0.09973749 0.09877394
  0.10138394 0.09869876 0.10005913 0.10031374]
 [0.09693889 0.09722548 0.10192381 0.10169763 0.10084271 0.0996525
  0.1032472  0.09916979 0.10041575 0.09888627]
 [0.0980396  0.09821044 0.10248298 0.10354185 0.10061047 0.09900817
  0.10149484 0.09858351 0.09814272 0.0998854 ]
 [0.09890349 0.09742936 0.10217131 0.10259444 0.1008717  0.09985524
  0.1030646  0.09859636 0.10032199 0.09619151]
 [0.09825766 0.09787394 0.10452209 0.10155906 0.09918603 0.09852759
  0.10516913 0.09931697 0.09907711 0.09651037]
 [0.09799155 0.09988558 0.10310994 0.10224719 0.1000355  0.09814214
  0.10195625 0.09867854 0.09974875 0.09

INFO:tensorflow:global_step/sec: 48.6198
INFO:tensorflow:probabilities = [[0.10068171 0.09998354 0.10294582 0.10155398 0.09964144 0.09785071
  0.10359631 0.09829649 0.09833519 0.0971148 ]
 [0.09797312 0.09945166 0.10157488 0.10246444 0.1002414  0.09772353
  0.10402191 0.09955578 0.09794818 0.09904514]
 [0.09826232 0.10001616 0.10112387 0.10161356 0.10199602 0.09553471
  0.10056163 0.09927734 0.10286707 0.09874726]
 [0.09853529 0.09997505 0.1015045  0.10134952 0.10041155 0.09738314
  0.1015151  0.09780157 0.10244516 0.09907916]
 [0.09995356 0.09787242 0.10109156 0.10209168 0.09985256 0.09991326
  0.10234027 0.09878577 0.09893617 0.09916268]
 [0.09856417 0.09895556 0.10203566 0.102377   0.09844857 0.09826824
  0.1040634  0.09942481 0.09868257 0.09918008]
 [0.10031544 0.09730516 0.10215773 0.10105557 0.10109709 0.09931941
  0.10160965 0.09902445 0.0999474  0.09816822]
 [0.09821455 0.09845077 0.10238641 0.10261338 0.10022843 0.0978293
  0.10460683 0.09851837 0.09905048 0.09810154]
 [0.0986

...

INFO:tensorflow:global_step/sec: 48.8486
INFO:tensorflow:probabilities = [[0.00002162 0.00000288 0.00013806 0.00007225 0.01501722 0.00001104
  0.00000492 0.00169834 0.00055474 0.98247886]
 [0.00000041 0.00000038 0.0000008  0.00001027 0.00001458 0.00001105
  0.         0.9993642  0.00000011 0.00059821]
 [0.00004853 0.00012978 0.00044459 0.00147082 0.968938   0.00078094
  0.0003638  0.00082038 0.00068716 0.02631594]
 [0.00000278 0.00019738 0.0000069  0.00019644 0.9479617  0.00009417
  0.00002926 0.0002093  0.00013306 0.05116909]
 [0.00000315 0.00005878 0.00015983 0.99758923 0.00003121 0.00063948
  0.00000105 0.00004156 0.00109566 0.00038017]
 [0.03052411 0.00620443 0.24679627 0.00137122 0.0192726  0.08312143
  0.5956084  0.00013891 0.01226302 0.00469958]
 [0.9999759  0.00000001 0.00000152 0.00000001 0.00000007 0.0000017
  0.00000174 0.00000425 0.00000024 0.00001437]
 [0.01204617 0.00110301 0.00427205 0.00020467 0.00250773 0.00254898
  0.07431142 0.00011198 0.9019023  0.00099164]
 [0.0000

INFO:tensorflow:loss = 0.13600281, step = 19901 (2.058 sec)
INFO:tensorflow:probabilities = [[0.00027166 0.00024625 0.00008228 0.00266552 0.00147502 0.99193114
  0.00104811 0.00013944 0.00211    0.00003049]
 [0.00001422 0.99073607 0.00034324 0.00005984 0.00205863 0.00000772
  0.00024063 0.00342629 0.00308837 0.00002509]
 [0.00026113 0.00001789 0.87854844 0.00202429 0.00009574 0.00039986
  0.08598472 0.00000083 0.03266501 0.00000218]
 [0.00001814 0.00004945 0.00000236 0.00155872 0.00011283 0.9790051
  0.01592858 0.00000012 0.00329067 0.00003402]
 [0.00042602 0.00000025 0.00001163 0.00000968 0.0052842  0.00002131
  0.00000292 0.00101958 0.04835873 0.94486564]
 [0.00000002 0.00000001 0.00000002 0.00000002 0.99996483 0.00000686
  0.00000047 0.00000102 0.00000454 0.00002208]
 [0.00029096 0.00070268 0.00018146 0.001698   0.00063674 0.00185873
  0.00000985 0.9309315  0.00034371 0.06334633]
 [0.998544   0.0000019  0.0004848  0.00010175 0.00000468 0.00035431
  0.00001213 0.00026797 0.000043   0

INFO:tensorflow:Saving checkpoints for 20000 into /tmp/mnist_convnet_model3\model.ckpt.
INFO:tensorflow:Loss for final step: 0.12891261.
INFO:tensorflow:Calling model_fn.
INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Starting evaluation at 2018-04-01-21:29:32
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Restoring parameters from /tmp/mnist_convnet_model3\model.ckpt-20000
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Finished evaluation at 2018-04-01-21:29:33
INFO:tensorflow:Saving dict for global step 20000: accuracy = 0.9647, global_step = 20000, loss = 0.10737269
{'accuracy': 0.9647, 'loss': 0.10737269, 'global_step': 20000}


SystemExit: 

d:\anaconda\envs\stable\lib\site-packages\IPython\core\interactiveshell.py:2918: UserWarning: To exit: use 'exit', 'quit', or Ctrl-D.
  warn("To exit: use 'exit', 'quit', or Ctrl-D.", stacklevel=1)
